In [1]:
%cd /home/yejin/data/projects/yejin/VerbCentric_RIS/ReferFormer

/data/projects/yejin/VerbCentric_RIS/ReferFormer


/home/yejin/.conda/envs/VerbCentric_RIS/lib/python3.9/site-packages/IPython/core/magics/osm.py:417: UserWarning: using dhist requires you to install the `pickleshare` library.
  self.shell.db['dhist'] = compress_dhist(dhist)[-100:]


## 1. manual 필터링 반영

In [18]:
import pandas as pd
import re
import json

In [31]:
selected_frames_df = pd.read_json("/home/yejin/data/dataset/VRIS/mbench/ytvos/selected_instances.jsonl", lines = True)
manual_selected = pd.read_json("manual_selected_frames.jsonl", lines = True)

In [32]:
selected_frames_df

segmentation  \
0  [[1081.0, 719.5, 1051.0, 719.5, 1050.5, 716.0,...   

                           bbox       area             file_name  height  \
0  [708.5, 156.5, 420.0, 563.0]  131357.25  00917dcfc4_00000.png     720   

   width  label category_name  \
0   1280     64         zebra   

                                           sentences  
0  {'tokens': ['a', 'zebra', 'on', 'the', 'right'...

In [ ]:
for i in range(len(manual_selected)):
    idx = manual_selected.loc[i, "index"]
    new_sent = manual_selected.loc[i, 'new_sent']

    if new_sent != "":
        new_sent_dict = {
            "tokens" : new_sent.split(' '),
            "raw" : new_sent,
            "sent" : re.sub('[^A-Za-z0-9\s]+', '', new_sent.lower())
        }
        selected_frames_df.at[idx, 'sentences'] = new_sent_dict

In [ ]:
manual_selected_frames = selected_frames_df.loc[manual_selected['index'].values]

In [31]:
manual_selected_frames.to_json("revised_frames.jsonl", orient='records', lines=True)

## 2. lmdb로 변환하기 위해 마스크 저장하기

In [2]:
import argparse
import os
import os.path as osp
import lmdb
import pyarrow as pa
import json
from tqdm import tqdm
import matplotlib.pyplot as plt
from skimage import io
import numpy as np
from shapely.geometry import Polygon, MultiPolygon
from matplotlib.collections import PatchCollection
from pycocotools import mask
import warnings
warnings.filterwarnings("ignore")

In [3]:
#jsonl 파일을 {index: json_obj, ... }형식으로

json_data = []

with open('revised_frames.jsonl', 'rb') as f:
    for line in f:
        json_data.append(json.loads(line))        

In [45]:
def getMask(ann):
    # return mask, area and mask-center
    if type(ann['segmentation'][0]) == list:  # polygon
        rle = mask.frPyObjects(ann['segmentation'], ann['height'],
                               ann['width'])
    else:
        rle = ann['segmentation']
    # for i in range(len(rle['counts'])):
    # print(rle)
    m = mask.decode(rle)
    m = np.sum(
        m, axis=2
    )  # sometimes there are multiple binary map (corresponding to multiple segs)
    m = m.astype(np.uint8)  # convert to np.uint8
    # compute area
    area = sum(mask.area(rle))  # should be close to ann['area']
    return {'mask': m, 'area': area}
    # # position
    # position_x = np.mean(np.where(m==1)[1]) # [1] means columns (matlab style) -> x (c style)
    # position_y = np.mean(np.where(m==1)[0]) # [0] means rows (matlab style)    -> y (c style)
    # # mass position (if there were multiple regions, we use the largest one.)
    # label_m = label(m, connectivity=m.ndim)
    # regions = regionprops(label_m)
    # if len(regions) > 0:
    # 	largest_id = np.argmax(np.array([props.filled_area for props in regions]))
    # 	largest_props = regions[largest_id]
    # 	mass_y, mass_x = largest_props.centroid
    # else:
    # 	mass_x, mass_y = position_x, position_y
    # # if centroid is not in mask, we find the closest point to it from mask
    # if m[mass_y, mass_x] != 1:
    # 	print 'Finding closes mask point ...'
    # 	kernel = np.ones((10, 10),np.uint8)
    # 	me = cv2.erode(m, kernel, iterations = 1)
    # 	points = zip(np.where(me == 1)[0].tolist(), np.where(me == 1)[1].tolist())  # row, col style
    # 	points = np.array(points)
    # 	dist   = np.sum((points - (mass_y, mass_x))**2, axis=1)
    # 	id     = np.argsort(dist)[0]
    # 	mass_y, mass_x = points[id]
    # 	# return
    # return {'mask': m, 'area': area, 'position_x': position_x, 'position_y': position_y, 'mass_x': mass_x, 'mass_y': mass_y}
    # # show image and mask
    # I = io.imread(osp.join(self.IMAGE_DIR, image['file_name']))
    # plt.figure()
    # plt.imshow(I)
    # ax = plt.gca()
    # img = np.ones( (m.shape[0], m.shape[1], 3) )
    # color_mask = np.array([2.0,166.0,101.0])/255
    # for i in range(3):
    #     img[:,:,i] = color_mask[i]
    # ax.imshow(np.dstack( (img, m*0.5) ))
    # plt.show()

def showMask(ann, image_dir, mask_dir):
   
    fig, ax = plt.subplots()
    I = io.imread(osp.join(image_dir, ann['file_name']))
    ax.imshow(I)

    M = getMask(ann)
    msk = M['mask']
    #msk = io.imread(osp.join(mask_dir, ann['file_name']))
    
    ax.imshow(msk, alpha = 0.5)
    ax.set_title(ann['sentences']['sent'])
    plt.show()



def saveMask(ann, mask_dir, seg_id):
    M = getMask(ann)
    msk = M['mask']
    height, width = msk.shape
    
    fig, ax = plt.subplots(figsize=(width / 100, height / 100), dpi=100)
    ax.imshow(msk, cmap='gray', vmin=0, vmax=1)

    save_path = f'{mask_dir}/{seg_id}'
    plt.axis('off')
    plt.subplots_adjust(left=0, right=1, top=1, bottom=0)  # Remove padding

    fig.savefig(save_path, dpi=100, bbox_inches='tight', pad_inches=0)
    
    plt.close(fig)

In [46]:
for i in range(len(json_data)):
    #showMask(json_data[i], image_dir = '/home/yejin/data/dataset/VRIS/mbench/ytvos/selected_frames', mask_dir = '/home/yejin/data/dataset/VRIS/mbench/ytvos/filtered_masks')
    saveMask(json_data[i], '/home/yejin/data/dataset/VRIS/mbench/ytvos/filtered_masks_segid', i)

In [ ]:
##############안 쓰는 함수!###################
# 마스크 저장
# annotation dictionary as input
def saveMask(annotation, mask_dir, seg_box='seg'):
    image_width = annotation['width']
    image_height = annotation['height']

    fig, ax = plt.subplots(figsize=(image_width / 100, image_height / 100), facecolor='black')  # figsize 단위는 인치, DPI 고려
    ax.set_facecolor('black')
    
    
    if seg_box == 'seg':
        polygons = []
        color = (1, 1, 1)
        
        if type(annotation['segmentation'][0]) == list:
            # polygon used for refcoco*
            for seg in annotation['segmentation']:
                poly = np.array(seg).reshape((int(len(seg) / 2), 2))
                polygons.append(Polygon(poly))

            p = PatchCollection(polygons,
                                facecolors=(1, 1, 1),
                                linewidths=0)
            ax.add_collection(p)

            # 축 범위를 이미지 크기에 맞게 설정
            ax.set_xlim(0, image_width)
            ax.set_ylim(0, image_height)
            
            # y축 방향 뒤집기 (이미지 좌표계와 일치)
            ax.invert_yaxis()
            
            # 플롯 표시
            #plt.axis('equal')  # 축 비율을 동일하게 설정
            #plt.show()

            #플롯 저장
            plt.axis('off')  # 축 숨김 (선택 사항)
            save_path = f'{mask_dir}/{annotation["file_name"]}'
            plt.savefig(save_path, bbox_inches='tight', pad_inches=0, facecolor='black')

for annotation in json_data:
    saveMask(annotation, mask_dir='/home/yejin/data/dataset/VRIS/mbench/ytvos/filtered_masks')
    